In [1]:
import csv
from math import log
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
import re
import sys

training_data_path = sys.argv[1]
testing_data_path = sys.argv[2]
output_path = sys.argv[3]

# training_data_path = "../data/amazon_train.csv"
# testing_data_path = "../data/amazon_test_public.csv"
# output_path = "../data/cs1160328.txt"

stop_words = set(stopwords.words('english'))
ps = PorterStemmer()

bigrams = {}

In [5]:
def stem_and_port(rows):
    for i in range(len(rows)):
        word_tokens = word_tokenize(rows[i][1])
        words = [w for w in word_tokens if not w in stop_words]
        result = []
        for word in words:
            result.append(ps.stem(word))
        rows[i][1] = result
    
        for i in range(len(result)-1):
            if (result[i]+' '+result[i+1]) not in bigrams:
                bigrams[result[i]+' '+result[i+1]] = 1
            else:
                bigrams[result[i]+' '+result[i+1]] += 1



def get_list_of_words(sentence):
#     words = re.split(';|,|\*|\n| ',sentence)
#     words = sentence.split(' ')
#     num = len(words)
#     for i in range(num-1):
#         if (words[])
#         words.append(words[i]+' '+words[i+1])
#     return words
    word_tokens = word_tokenize(sentence)
#     return word_tokens
    words = [w for w in word_tokens if not w in stop_words]
    result = []
    for word in words:
        result.append(ps.stem(word))
    
    for i in range(len(result)-1):
        new_word = result[i]+' '+result[i+1]
        if (new_word) not in bigrams:
            bigrams[new_word] = 1
        else:
            bigrams[new_word] += 1

    return result

def get_list_of_words_bigrams(words):
#     word_tokens = word_tokenize(sentence)
#     words = [w for w in word_tokens if not w in stop_words]
#     result = []
#     for word in words:
#         result.append(ps.stem(word))
        
    num = len(words)
    for i in range(num-1):
        new_word = words[i]+' '+words[i+1]
        if(new_word in bigrams):
            if (bigrams[new_word] > 12):
                words.append(new_word)
    return words

def load_train_data(path):
    total_reviews = 0
    num_reviews = [0,0,0,0,0]
    num_words = [0,0,0,0,0]
    dictionary = {1:{},2:{},3:{},4:{},5:{}}
    vocab = {}
    total_words_in_vocab = 0
    with open(path, 'r') as csvfile:
        spamreader = csv.reader(csvfile, delimiter=',')
        spamreader = list(spamreader)
        stem_and_port(spamreader)
#         for row in spamreader:
#             words = get_list_of_words(row[1])
#         spamreader = csv.reader(csvfile, delimiter=',')
        for row in spamreader:
#             print(row[1])
            total_reviews += 1
            rating = int(float(row[0]))
            num_reviews[rating - 1] += 1
            words = get_list_of_words_bigrams(row[1])
            dict = {}
            for word in words:
                
                if word not in vocab:
                    vocab[word] = 1
                    total_words_in_vocab += 1
                else:
                    vocab[word] += 1
                    
                if word not in dictionary[rating]:
                    dictionary[rating][word] = 1
                else:
                    dictionary[rating][word] += 1
                    
                num_words[rating-1] += 1
                
    return num_reviews,total_reviews,dictionary,total_words_in_vocab,vocab,num_words


def load_test_data(path):
    data = []
    with open(path, 'r') as csvfile:
        spamreader = csv.reader(csvfile, delimiter=',')
        for row in spamreader:
            data.append(get_list_of_words_bigrams(word_tokenize(row[1])))
    return data

def predict(testing_examples,dictionary,num_words,total,vocab_len,vocab):
    ratings = []
    for list_of_words in testing_examples:
        probabs = []
        for rating in range(1,6):
            probab = log(num_words[rating-1]/total)
            for word in list_of_words:
                if word in dictionary[rating]:
                    probab += log((dictionary[rating][word] + 1)/ (num_words[rating-1] + vocab_len + 1))/log(vocab[word]+2)
                else:
                    if word in vocab:
                        probab += log(1/ (num_words[rating-1] + vocab_len + 1))/log(vocab[word]+2)
                    else:
                        probab += log(1/ (num_words[rating-1] + vocab_len + 1))/log(2)
            probabs.append(probab)
        best_rating  = probabs.index(max(probabs))+1
        ratings.append(best_rating)
    return ratings

In [3]:
num_reviews, tot, dictionary,vocab_len,vocab,num_words = load_train_data(training_data_path)

['album', 'stevi', ';', 'decad', 'inspir', 'inspir', 'song', ',', 'arrang', ',', 'melodi', 'lyric', ',', 'total', 'sold', 'offer', 'bland', ',', 'aw', ',', 'complet', 'uninspir', 'product', ',', 'continu', 'throughout', 'day.or', '?', 'well', ',', 'partial', 'true', ',', 'except', 'one', 'thing', ';', 'stevi', 'alway', 'sell', 'album', '.', 'ye', ',', 'amaz', ',', 'beauti', 'way', ',', 'stevi', 'alway', 'commerci', 'artist', '.', 'thi', 'album', 'reflect', ';', 'becom', 'interest', 'digit', 'synth', 'one', '.', 'and', ',', 'unfortunatley', ',', 'creativ', 'digit', 'synth', 'analogu', '.', 'not', ',', 'album', 'featur', 'great', 'drum', 'either', '!', 'It', "'s", 'drum', 'machin', '.', 'A', 'disast', '?', 'well', ',', 'arrang', 'sometim', 'mess', '.', 'not', 'quit', 'disast', ',', 'album', "n't", 'live', 'breath', 'like', 'classic', 'stevi', '.', 'In', '70', "'s", ',', 'stevi', 'would', 'make', 'song', 'play', 'everi', 'instrument', 'live', 'breath', 'like', 'real', 'funk', 'jam', '.', 

['I', 'guess', 'say', 'love', 'music', 'fond', '``', 'pet', 'sound', "''", 'almost', 'paradox', 'sinc', 'brian', 'wilson', "'s", 'skywritten', 'testament', 'embodi', 'everyth', "'s", 'good', 'pop', 'music', ':', 'excel', 'tune', ',', 'lyric', ',', 'vocal', 'harmoni', 'even', 'flourish', 'add', 'wonder', ',', 'dreami', 'lush', 'feel', '.', '``', 'you', 'still', 'believ', "''", ',', "''", 'god', 'know', "''", '``', 'I', 'know', "'s", 'answer', "''", 'certainli', 'among', 'favorit', 'song', 'ad', 'proof', 'good', 'music', 'tower', 'decad', 'without', 'lose', 'trace', 'greatness-', "''", 'forev', 'chang', "''", ',', "''", 'odessey', 'oracl', "''", '``', 'pet', 'sound', "''", 'alway', 'great', ',', 'come', 'may', '.']
['thi', 'album', 'one', 'first', 'album', 'featur', 'scratchin', "'", 'heavier', 'guitar', '.', 'I', 'like', 'african', 'bongo', 'type', 'sound', 'lace', 'jazzi', 'guitar', 'lick', '.', 'the', 'album', 'quit', 'split', 'real', 'heavi', 'sound', 'real', 'mellow', 'type', 'sound

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




['I', 'young', 'teenag', 'wait', "'18", "'", 'album', 'came', '.', 'In', 'addit', ',', 'fold', 'record', 'player', 'high', 'school', 'attend', ',', ',', 'well', 'killer', ',', 'would', 'one', 'mani', 'group', 'album', 'expos', '.', 'A', 'year', 'back', ',', 'I', 'purchas', 'first', '2', 'album', 'AC', 'band', ',', 'alot', 'differ', '.', 'pretti', 'for', 'you', 'name', 'album', 'escap', ',', 'interest', 'record', ':', 'know', 'want', 'rock', ',', 'also', 'knew', 'need', 'nich', ',', 'album', 'brought', 'forefront', '.', 'have', 'album', 'like', 'own', 'copi', 'one', 'tale', 'from', 'crypt', 'book', ',', 'audio', 'form', '.', 'face', ',', 'the', 'exorcist', "n't", 'even', 'come', 'yet', '.', 'thi', 'album', 'hold', 'well', 'year', '.', 'I', 'wait', 'price', 'goe', 'back', 'purchas', '.', 'the', 'interest', 'thing', 'I', 'love', 'album', 'amidst', 'dark', 'theme', ',', '(', 'black', 'juju', ')', 'they', 'excel', 'version', 'rolf', 'harri', "'s", 'sun-a-ris', ',', 'give', 'us', 'sli', 'wi

['I', 'realli', 'enjoy', 'disc', '&', '#', '34', ';', 'the', 'girl', 'ipanema', '&', '#', '34', ';', 'track', 'well', '.', 'veri', 'strong', 'effort', '.']
['everi', 'time', 'orb', 'releas', 'someth', 'new', '.', 'get', 'bash', 'orb', 'everybodi', 'want', '.', 'mostli', 'everi', 'album', 'differ', 'territor', 'orb', 'explor', 'neccicarili', 'envolv', 'sound', 'album', 'hand', '.', 'pomm', 'fritz', 'came', 'along', 'peopl', 'wine', 'LX', 'finnali', 'lost', 'head', '..', 'well', 'understand', ',', 'highli', 'ambient', 'heavi', 'wierd', 'kiddi', 'like', 'sampl', '(', 'love', ')', 'orbv', 'terrivm', 'came', 'peopl', 'like', '&', 'quot', ';', 'well', 'hard', 'live', 'standard', 'perfect', 'creat', '&', 'quot', ';', 'despit', 'fact', 'love', 'everi', 'moment', 'orbvu', 'terrivm', '.', 'orblivion', 'hit', 'obviou', 'drum', 'n', 'bass', 'influenc', 'peopel', 'cri', 'orb', "n't", 'music', 'want', '.', 'even', 'though', 'orblivion', 'best', 'orb', 'track', 'ever', '.', 'cydonia', 'hit', 'peopl',

['the', 'rocki', 'mountain', 'collect', '(', '1996', ')', '2-disc', 'solo', 'career-span', 'overview', 'john', 'denver', "'s", 'beauti', 'inspir', 'music', '.', 'It', 'begin', 'leav', ',', 'On', 'A', 'jet', 'plane', 'cover', 'song', 'like', 'rocki', 'mountain', 'high', ',', 'take', 'Me', 'home', 'countri', 'road', ',', 'sunshin', 'On', 'My', 'shoulder', ',', 'calypso', ',', 'wild', 'montana', 'ski', 'emmyl', 'harri', ',', 'poem', 'prayer', 'and', 'promis', ',', 'the', 'eagl', 'and', 'the', 'hawk', ',', 'starwood', 'In', 'aspen', ',', 'thank', 'god', 'I', "'m", 'A', 'countri', 'boy', ',', 'perhap', 'love', 'placido', 'domingo', ',', 'more.th', 'song', 'collect', 'highlight', 'songwrit', ',', 'guitar', 'play', 'sing', 'talent', 'special', 'american', 'care', 'deepli', 'earth', ',', 'natur', ',', 'wildlif', 'fellow', 'man', '.', 'the', 'music', 'mostli', 'folk/pop', ',', 'acoust', 'guitar', 'domin', 'song', 'natur', ',', 'love', 'self-discoveri', 'highest', 'qualiti', '.', 'It', "'s", 'ho

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['one', 'favorit', 'juda', 'priest', "'s", 'album', '.', 'buy', 'like', 'later', 'music', '.']
['ra', 'kass', "'", 'second', 'major', 'label', 'album', 'pretti', 'good', '.', 'I', 'bought', 'year', 'came', 'caus', 'I', 'heard', 'spit', 'song', 'I', 'highli', 'impress', 'mc', 'abil', '(', 'one', 'top', '5', 'ask', ')', '.', 'So', 'I', 'thought', 'cd', 'would', 'much', 'better', '.', 'It', 'good', 'track', 'outshin', 'product', 'great', 'lyric', 'abil', '&', 'deliveri', '.', 'stu', 'B', 'doo', '&', 'kiev', '4', 'song', ',', 'flip', '2', ',', '&', 'toxic', ',', '12', ',', 'big', 'jaz', ',', 'eazi', 'Mo', 'bee', '1', '.', 'He', 'obsess', 'master', 'P', 'album', 'though', ',', 'constantli', 'say', '``', 'unnhhh', "''", 'incorporationg', 'bunch', 'song', '&', 'skit', ',', 'nevertheless', 'album', 'decent', 'fan', 'pick', '.', 'featur', 'quit', 'cat', 'well', '.', 'It', '1', 'almost', 'classic', ',', '2', 'I', 'skip', ',', '5', '6', 'ok', ',', 'other', 'good', ',', 'great.', '#', '2', '-', '8

['the', 'earliest', 'work', 'pac', ',', 'beat', 'good', 'album', 'could', 'better.not', '2pac', "'s", 'best', 'album', ',', 'definetli', 'classic', 'hit', 'like', 'keep', 'ya', 'head', ',', 'get', 'around.it', 'similar', '2pacalysp', 'aint', 'better', 'world', 'eyez', '7dt.if', "have'nt", 'got', 'world', 'eyez', '7', 'day', 'theori', 'suggest', 'u', 'get', 'one', '.']
['newcom', 'nativ', 'tongu', '(', 'De', 'La', 'soul', ',', 'jungl', 'brother', '&', 'A', 'tribe', 'call', 'quest', ')', 'famili', ',', 'black', 'sheep', 'drop', 'debut', ',', 'A', 'wolf', 'In', 'sheep', "'s", 'cloth', ',', 'one', 'trait', 'pertin', ',', 'lyric', 'skill', '.', 'dream', 'begin', 'album', ',', 'comed', 'effort', '``', 'U', 'mean', 'I', "'m", 'not', "''", 'disrespect', 'gangster', 'rap', "'s", 'street', 'graphic', 'tale', '.', '``', 'La', 'M', '&', 'eacut', ';', 'nage', "''", 'featur', 'q-tip', 'good', 'song', 'pertain', 'sex', 'dre', 'partner', 'mista', 'lawng', 'alter', 'ego', 'sugar', 'dick', 'daddi', 'sho

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [6]:
test_data = load_test_data(testing_data_path)

In [7]:
print(tot)

32352


In [8]:
predictions = predict(test_data,dictionary,num_words,tot,vocab_len,vocab)
x = {1:0,2:0,3:0,4:0,5:0}
for pr in predictions:
    x[pr] += 1
print(x)

{1: 0, 2: 0, 3: 2, 4: 96, 5: 16078}


In [9]:
with open(output_path, 'w') as f:
    for item in predictions:
        f.write("%s\n" % item)